# Linear vs non-linear learning

Compare a _linear SVM model_ to a _kernel SVM model_ on the UCI Adult dataset: 
- given features collected from the census, predict whether a person has a salary greater or smaller than 50K/yr
- for the kernel, use the **Gaussian kernel with ** $\gamma = .2$ (selected by hand): $$ \kappa(\mathbf{x}, \mathbf{y}) = \kappa(\mathbf{x} - \mathbf{y}) = \exp\left( - \gamma \|\mathbf{x} - \mathbf{y}\|_2^2 \right) $$

Predictions using the linear SVM model are given by $$h(\mathbf{x}) = \text{sign}(\langle \mathbf{w}, \mathbf{x} \rangle + b).$$
and predictions using the kernel SVM model are given by $$h(\mathbf{x}) = [\kappa(\mathbf{x}, \mathbf{x}_1), \ldots, \kappa(\mathbf{x}, \mathbf{x}_n)] \boldsymbol{\alpha}$$

The loss function for the linear SVM model is:
$$
     f(\mathbf{w}, b) = \frac{1}{n} \sum_{i=1}^n \big(1 - y_i (\langle \mathbf{w}, \mathbf{x}_i \rangle + b)\big)_+ + \frac{\lambda}{2} \|\mathbf{w}\|_2^2.
$$
The loss function for the kernel SVM model is:
$$
    f(\alpha) = \frac{1}{n} \sum_{i=1}^n \big(1 - y_i (\mathbf{K} \boldsymbol{\alpha})_i \big)_+ + \frac{\lambda}{2} \boldsymbol{\alpha}^T \mathbf{K} \boldsymbol{\alpha}.
$$

We also use approximate kernel methods (Nystrom and Random Feature Maps) to speed up the kernel learning 

In [1]:
import numpy as np
from numpy.linalg import svd, norm
import math
import random
from sklearn import preprocessing
from sklearn.decomposition import TruncatedSVD
from sklearn.datasets import load_svmlight_file
from sklearn import preprocessing
from sklearn.metrics import accuracy_score
from sklearn.metrics.pairwise import rbf_kernel
import matplotlib.pyplot as plt
from functools import reduce
import time

# for reproducibility
random.seed(4000)

### Load the training data, do the z-transform to make the features look more like standard Gaussians

In [3]:
trainfname = "a9a.txt"
Xtrain, ytrain = load_svmlight_file(trainfname)
Xtrain = Xtrain.toarray()[:,:122] # densifies *and* makes it an array instead of a matrix, and remove the last column because that feature doesn't exist in the test data
ytrain = np.expand_dims(ytrain, 1)

testfname = "a9a.t"
Xtest, ytest = load_svmlight_file(testfname)
Xtest = Xtest.toarray() # densifies *and* makes it an array instead of a matrix
ytest = np.expand_dims(ytest, 1)

scaler = preprocessing.StandardScaler().fit(Xtrain)
Xtrain = scaler.transform(Xtrain)
Xtest = scaler.transform(Xtest)

### Set some useful quantities

In [10]:
ntrain,d = Xtrain.shape # problem dimensions for linear model
w1 = np.zeros((d+1,)) # initialize linear parameters (w, b) at zero
regparam = 1/ntrain # for both methods set the regularization parameter

# Linear Model

### Define the functions used for fitting the kernel model

In [5]:
def linear_loss(X, y, w):
    d = X.shape[1]
    coeffs = np.reshape(w[:-1], (d,1))
    bias = w[-1]
    e = (1 - (y*(X@coeffs) + bias))
    e[e < 0] = 0
    return 1/ntrain*np.sum(e)

def linear_subgradloss(X, y, w):
    d = X.shape[1]
    coeffs = np.reshape(w[:-1], (d,1))
    bias = w[-1]
    e = 1 - (y*(X@coeffs)+ bias)
    g = -1/ntrain * (y*e).T @ np.hstack((X, np.ones((ntrain,1))))
    return g.T

def linear_subgradreg(w):
    temp = w
    temp[-1] = 0
    return temp

def linear_heavyball(X, y, loss, subgradloss, subgradreg, regparam, w1, T, beta, gamma=0.9):
    trajectory = [w1]
    losshistory = [(1, loss(X, y, trajectory[-1]))]
    mu = 0*w1
    for iternum in range(1, T+1):
        stepsize = 1/beta
        wcur = trajectory[-1]
        mu = gamma * mu + stepsize * (subgradloss(X, y, wcur) + regparam*subgradreg(wcur))
        trajectory.append(wcur - mu)
        if (iternum % 100 == 0):
            losshistory.append((iternum, loss(X, y, trajectory[-1])) )
            print("[%d/%d]: loss %f" % (iternum, T, losshistory[-1][1]))
    return trajectory, losshistory

def linear_empiricalaccuracy(X, y, w):
    d = X.shape[1]
    coeffs = np.reshape(w[:-1], (d,1))
    bias = w[-1]
    return accuracy_score(np.sign(X@coeffs + bias), y)

### Fit the linear model and report its training and testing accuracies

In [6]:
T = 5000
beta = 1000
w1 = np.zeros((d+1, 1))

tic = time.perf_counter()
trajectory, losshistory = linear_heavyball(Xtrain, ytrain, linear_loss, linear_subgradloss, linear_subgradreg, regparam, w1, T, beta, gamma=0.9)
toc = time.perf_counter()

print(f"Training linear model over %d iterations took {toc - tic:.1f} seconds" % T)

[100/5000]: loss 0.739154
[200/5000]: loss 0.734085
[300/5000]: loss 0.732766
[400/5000]: loss 0.732320
[500/5000]: loss 0.732128
[600/5000]: loss 0.732031
[700/5000]: loss 0.731976
[800/5000]: loss 0.731940
[900/5000]: loss 0.731916
[1000/5000]: loss 0.731898
[1100/5000]: loss 0.731884
[1200/5000]: loss 0.731873
[1300/5000]: loss 0.731864
[1400/5000]: loss 0.731856
[1500/5000]: loss 0.731850
[1600/5000]: loss 0.731845
[1700/5000]: loss 0.731840
[1800/5000]: loss 0.731836
[1900/5000]: loss 0.731832
[2000/5000]: loss 0.731829
[2100/5000]: loss 0.731826
[2200/5000]: loss 0.731824
[2300/5000]: loss 0.731822
[2400/5000]: loss 0.731820
[2500/5000]: loss 0.731818
[2600/5000]: loss 0.731816
[2700/5000]: loss 0.731815
[2800/5000]: loss 0.731814
[2900/5000]: loss 0.731813
[3000/5000]: loss 0.731812
[3100/5000]: loss 0.731811
[3200/5000]: loss 0.731810
[3300/5000]: loss 0.731809
[3400/5000]: loss 0.731809
[3500/5000]: loss 0.731808
[3600/5000]: loss 0.731807
[3700/5000]: loss 0.731807
[3800/5000

In [7]:
linear_train_accuracy = 100*linear_empiricalaccuracy(Xtrain, ytrain, trajectory[-1])
linear_test_accuracy = 100*linear_empiricalaccuracy(Xtest, ytest, trajectory[-1])
print(f"The final test/train accuracies are %.2f/%.2f" % (linear_train_accuracy, linear_test_accuracy))

The final test/train accuracies are 73.73/73.58


# Exact Kernel Model

### Construct the training and testing kernel matrices

The kernel matrix used in training, $\mathbf{K}_{\text{train}} \in \mathbb{R}^{n_{\text{train}} \times n_{\text{train}}}$, satisfies
$$
K_{\text{train},ij} = \kappa(\mathbf{x}_i, \mathbf{x}_j)
$$

The kernel matrix used at test time, $\mathbf{K}_{\text{test}} \in \mathbb{R}^{n_{\text{test}} \times n_{\text{train}}}$, satisfies
$$
\mathbf{K}_{\text{test}} = \begin{pmatrix}
 \kappa(\mathbf{x}_{\text{test},1}, \mathbf{x}_{\text{train},1}) & \ldots & \kappa(\mathbf{x}_{\text{test},n_{\text{train}}}, \mathbf{x}_{\text{train},n_{\text{train}}}) \\
 & \vdots & \\
 \kappa(\mathbf{x}_{\text{test},n_{\text{test}}}, \mathbf{x}_{\text{train},1}) & \ldots & \kappa(\mathbf{x}_{\text{test},n_{\text{train}}}, \mathbf{x}_{\text{train},n_{\text{train}}})
\end{pmatrix}
$$

In [11]:
# Handtuned gamma (gamma = 1/(2*sigma**2))
tic = time.perf_counter()
Ktrain = rbf_kernel(Xtrain, Xtrain, gamma=.2)
Ktest = rbf_kernel(Xtest, Xtrain, gamma=.2)
toc = time.perf_counter()
print(f"Computing the train and testing kernels took {toc - tic:.1f} seconds")

Computing the train and testing kernels took 21.0 seconds


### Define the functions used for fitting the exact kernel model

In [13]:
def kernel_loss(K, y, alpha):
    """computes 1/n \sum_{i=1}^n (1 - y_i(K alpha)_i)_+"""
    ntrain = K.shape[0]
    e = (1 - y * (K@alpha))
    e[ e <0 ] = 0
    return 1/ntrain*np.sum(e)

def kernel_subgradloss(K, y, alpha):
    """ 1/n \sum_{i=1}^n sgn((1 - y_i(K*alpha)_i)_+))* (-y_i K_i)"""
    ntrain = K.shape[0]
    e = (1 - y * (K@alpha))
    e[ e <0 ] = 0
    return 1/ntrain * (-(e*y).T @ K).T

def kernel_subgradreg(K, alpha):
    return K @ alpha

# use heavy-ball (plain subgradient is **slow** by about 10x)
def kernel_heavyball(K, y, loss, subgradloss, subgradreg, regparam, alpha1, T, beta, gamma=0.9):
    trajectory = [alpha1]
    losshistory = [(1, loss(K, y, trajectory[-1]))]
    mu = 0*alpha1
    for iternum in range(1, T+1):
        stepsize = 1/beta
        prevalpha = trajectory[-1]
        loss_subgrad = subgradloss(K, y, prevalpha)
        mu = gamma * mu + stepsize*(loss_subgrad + regparam*subgradreg(K, prevalpha))
        trajectory.append(prevalpha - mu)
        if (iternum % 10 == 0):
            losshistory.append((iternum, loss(K, y, trajectory[-1])) )
            print("[%d/%d]: loss %f" % (iternum, T, losshistory[-1][1]))
    return trajectory, losshistory

def kernel_empiricalaccuracy(K, y, alpha):
    return accuracy_score(np.sign(K@alpha), y)

### Fit the exact kernel model and report its training and testing accuracies

In [14]:
T = 100
beta = 2000 # need small stepsize because the fact we use K in each iteration implies we'll make large changes otherwise
ntrain = Ktrain.shape[0]
alpha1 = np.zeros((ntrain,1))

tic = time.perf_counter()
trajectory, losshistory = kernel_heavyball(Ktrain, ytrain, kernel_loss, kernel_subgradloss, kernel_subgradreg, regparam, alpha1, T, beta, gamma=0.9)
toc = time.perf_counter()

print(f"Training over %d iterations took {toc - tic:.1f} seconds" % T)

[10/100]: loss 0.999985
[20/100]: loss 0.999957
[30/100]: loss 0.999925
[40/100]: loss 0.999890
[50/100]: loss 0.999855
[60/100]: loss 0.999820
[70/100]: loss 0.999785
[80/100]: loss 0.999750
[90/100]: loss 0.999715
[100/100]: loss 0.999680
Training over 100 iterations took 145.5 seconds


In [15]:
exact_kernel_train_accuracy = 100*kernel_empiricalaccuracy(Ktrain, ytrain, trajectory[-1])
exact_kernel_test_accuracy = 100*kernel_empiricalaccuracy(Ktest, ytest, trajectory[-1])
print(f"The final train/test accuracies are %.2f/%.2f" % (exact_kernel_train_accuracy, exact_kernel_test_accuracy))

The final train/test accuracies are 93.64/82.40


# Approximate Kernel Methods using Nystrom and Random Feature Map approximations

### Construct Nystrom and Random Feature Map approximations to the training kernel matrix

In [16]:
# Form a Nystrom approximation (use 400 landmark points because it gives sufficient accuracy in the learning application, and is fast)
ell = 400
Cindices = np.random.permutation(ntrain)[:ell]
landmarkpoints = Xtrain[Cindices,:]
C = rbf_kernel(Xtrain, landmarkpoints, gamma=.2)
W = rbf_kernel(landmarkpoints, landmarkpoints, gamma=.2)
Winv = np.linalg.pinv(W)

# Show relative error of the kernel approximation (as a sanity check: aless than 1 is good)
Kapprox = C @ Winv @ C.T
print("Relative Frobenius norm error of the Nystrom kernel approximation: ", 
      np.linalg.norm(Ktrain - Kapprox, ord='fro')/np.linalg.norm(Ktrain, ord='fro'))

Relative Frobenius norm error of the Nystrom kernel approximation:  0.9518925960498662


In [17]:
# Form a random feature map approximation for the Gaussian kernel exp(-||x-y||^2/(2\sigma^2))
# phitilde maps x to D-dimensional vector where each entry takes the form sqrt(2/D) * cos(<w_i, x> + b_i),
# where the w_i vectors are distributed N(0,1) and the b_i are distributed Uniform[0,2*pi]

# set bandwidth and number of random features to use
gamma = .2  # handtuned value
sigma = np.sqrt(1/(2*.2)) # corresponding bandwidth
Drfm = 1000

# Sample the random frequencies and phases used in the random feature map, take D large
Wf = sigma*np.random.randn(Drfm, d)
bp = np.random.rand(Drfm,1)

def phitilde_rfm(X, W, b):
    D = W.shape[0]
    return np.sqrt(2/D) * np.cos(X @ W.T + np.repeat(b.T, X.shape[0], 0))

Phi = phitilde_rfm(Xtrain, Wf, bp) # the random feature map
Kapprox = Phi @ Phi.T # the kernel approximation corresponding to the random feature map

# the relative approximation error of the approximate kernel to the true kernel
print("Relative Frobenius norm error of the Gaussian random feature map kernel approximation: ", 
      np.linalg.norm(Ktrain - Kapprox, ord='fro')/np.linalg.norm(Kapprox))

Relative Frobenius norm error of the Gaussian random feature map kernel approximation:  0.9665463797031626


### Define functions used for fitting the approximate kernel logistic regression model using Nystrom kernel approximation

In [18]:
def nystrom_kernel_loss(C, Winv, y, alpha):
    """approximates 1/n \sum_{i=1}^n (1 - y_i(K alpha)_i)_+"""
    e = (1 - y * (C@(Winv@(C.T@alpha))))
    e[ e <0 ] = 0
    return 1/ntrain*np.sum(e)

def nystrom_kernel_subgradloss(C, Winv, y, alpha):
    """approximates 1/n \sum_{i=1}^n sgn((1 - y_i(K*alpha)_i)_+))* (-y_i K_i)"""
    e = (1 - y * (C@(Winv@(C.T@alpha))))
    e[ e <0 ] = 0
    return -1/ntrain * C @ (Winv @ (C.T @ (e*y)))

def nystrom_kernel_subgradreg(C, Winv, alpha):
    """ approximates the subgradient of the regularizer, K alpha"""
    return C @ (Winv @ (C.T @ alpha))

# use heavy-ball (plain subgradient is **slow** by about 10x)
def nystrom_kernel_heavyball(C, Winv, y, loss, subgradloss, subgradreg, regparam, alpha1, T, beta, gamma=0.9):
    trajectory = [alpha1]
    losshistory = [(1, loss(C, Winv, y, trajectory[-1]))]
    mu = 0*alpha1
    for iternum in range(1, T+1):
        stepsize = 1/beta
        prevalpha = trajectory[-1]
        loss_subgrad = subgradloss(C, Winv, y, prevalpha)
        mu = gamma * mu + stepsize*(loss_subgrad + regparam*subgradreg(C, Winv, prevalpha))
        trajectory.append(prevalpha - mu)
        if (iternum % 10 == 0):
            losshistory.append((iternum, loss(C, Winv, y, trajectory[-1])) )
            print("[%d/%d]: loss %f" % (iternum, T, losshistory[-1][1]))
    return trajectory, losshistory

def kernel_empiricalaccuracy(K, y, alpha):
    return accuracy_score(np.sign(K@alpha), y)

### Fit the Nystrom kernel method and report its training and test accuracies

In [19]:
T = 100
beta = 2000 # need small stepsize because the fact we use K in each iteration implies we'll make large changes otherwise
alpha1 = np.zeros((ntrain,1))

tic = time.perf_counter()
trajectory, losshistory = nystrom_kernel_heavyball(C, Winv, ytrain, 
                                                   nystrom_kernel_loss, 
                                                   nystrom_kernel_subgradloss, 
                                                   nystrom_kernel_subgradreg, 
                                                   regparam, alpha1, T, beta, gamma=0.9)
toc = time.perf_counter()

print(f"Training over %d iterations took {toc - tic:.1f} seconds" % T)
nystrom_kernel_train_accuracy = 100*kernel_empiricalaccuracy(Ktrain, ytrain, trajectory[-1])
nystrom_kernel_test_accuracy = 100*kernel_empiricalaccuracy(Ktest, ytest, trajectory[-1])
print(f"The final train/test accuracies are %.2f, %.2f" % (nystrom_kernel_test_accuracy, nystrom_kernel_test_accuracy))

[10/100]: loss 0.999998
[20/100]: loss 0.999993
[30/100]: loss 0.999988
[40/100]: loss 0.999982
[50/100]: loss 0.999976
[60/100]: loss 0.999971
[70/100]: loss 0.999965
[80/100]: loss 0.999959
[90/100]: loss 0.999954
[100/100]: loss 0.999948
Training over 100 iterations took 4.9 seconds
The final train/test accuracies are 80.67, 80.67


### Fit the RFM kernel method and report its training and test accuracies

The advantage of the RFM method is that we can do regression over the approximate features $\tilde{\phi}$ **directly** and efficiently because the number of random features is small compared to the number of features in the true feature maps. Thus we can just do a regular linear regression.

In [20]:
T = 200
beta = 300
w1 = np.zeros((Drfm+1, 1))

tic = time.perf_counter()
trajectory, losshistory = linear_heavyball(Phi, ytrain, linear_loss, linear_subgradloss, linear_subgradreg, regparam, w1, T, beta, gamma=0.9)
toc = time.perf_counter()

print(f"Training linear model over %d iterations took {toc - tic:.1f} seconds" % T)

[100/200]: loss 1.017412
[200/200]: loss 1.017225
Training linear model over 200 iterations took 15.6 seconds


In [21]:
rfm_train_accuracy = 100*linear_empiricalaccuracy(Phi, ytrain, trajectory[-1])
rfm_test_accuracy = 100*linear_empiricalaccuracy(phitilde_rfm(Xtest, Wf, bp), ytest, trajectory[-1])
print(f"The final test/train accuracies are %.2f/%.2f" % (rfm_train_accuracy, rfm_test_accuracy))

The final test/train accuracies are 75.92/76.38


# Example of Random Feature Map for the polynomial kernel $\langle \mathbf{x}, \mathbf{y} \rangle^r$

Note that we aren't applying the polynomial kernel to this particular application, so this is just a synthetic illustration

In [30]:
# The rfm for this kernel, phitilde, maps x to a D dimensional vector where each entry takes the form 1/sqrt(D) * Prod(<x,eps_i>, i=1,...,r)
# where the eps_i are independent vectors of random signs
# In this example, r = 2

# create a sample training set
X = np.random.randn(3,d)

# sample the random vectors used in the random feature map, take D large
Dpoly = 400000
W1 = np.sign(2*np.random.rand(Dpoly, d)-1)
W2 = np.sign(2*np.random.rand(Dpoly, d)-1)

# computes the n-by-D random feature map matrix PhiTilde, whose rows contain
# phitilde(x_i), the random features for the ith training example
def phitilde_poly(X, W1, W2):
    D = W1.shape[0]
    return 1/np.sqrt(D) * (X @ W1.T) * (X @ W2.T)

Phi = phitilde_poly(X, W1, W2) # the random feature map
Ktilde = Phi @ Phi.T # the kernel approximation corresponding to the random feature map
K = np.power(X @ X.T, 2) # the true polynomial kernel

# the relative approximation error of the approximate kernel to the true kernel
print("Relative Frobenius norm error of the polynomial random feature map kernel approximation on synthetic data with r=2: ", 
      np.linalg.norm(K - Ktilde, ord='fro')/np.linalg.norm(K))

Relative Frobenius norm error of the polynomial random feature map kernel approximation on synthetic data with r=2:  0.005978204979084676
